In [ ]:
import marimo as mo

In [ ]:
from ortools.sat.python import cp_model
import math
import time
import pprint

# 極大ナップサック問題

## 問題

正整数の配列 $a = [ a_1, \dots, a_n]$ と整数 $\tau$ が与えられる.
このとき $a$ の部分配列でその**総積**が $\tau$ 以下になるもので極大なものを全て列挙せよ.

## 定式化

$x = [x_1, \dots, x_n]$ を 0-1 決定変数とする.
$x_i$ が $1$ のとき $a_i$ を採用し, $0$ のとき採用しない.
また, 決定変数 $y = [y_1, \dots, y_n]$ を用意し $y_i = (a_i - 1) x_i + 1$ を課す.
こうすると $y_i$ は $x_i$ が $1$ のとき $a_i$ を値に取り, $0$ のとき $1$ を値にとる.
同様に $z_i = (a_i - 1) (1 - x_i) + 1$ とおく.
こちらは $y_i$ とは逆に採用されてない $a_i$ に対してだけ値 $a_i$ を取り, 採用されているものについては $1$ を取る.

Google OR-Tools は整数変数の積をそのまま扱えるため, 線形ではない定式化を行う.

- $\prod_{i=1}^n y_i \leq \tau$: 採用した $a_i$ の積が $\tau$ を超えない.
- $z_j \prod_{i=1}^n y_i > \tau (1 - x_j) \quad (\forall j = 1, \dots, n)$: 採用しなかった $a_j$ を掛けたら $\tau$ を超えてしまう.

また, Google OR-Tools の CP-SAT ソルバーは目的関数を設定しない場合,
実行可能解を全て求めるよう指示できるのでそれを使って全ての極大元を求める.

## 実装

In [ ]:
class SolutionPrinter(cp_model.CpSolverSolutionCallback):

    def __init__(self, a, solution: list[cp_model.IntVar]):
        cp_model.CpSolverSolutionCallback.__init__(self)
        self.__solution = solution
        self.__a = a
        self.__solution_count = 0
        self.__all_solutions = []
        self.__start_time = time.time()

    @property
    def solution_count(self) -> int:
        return self.__solution_count

    @property
    def all_solutions(self):
        return self.__all_solutions

    def on_solution_callback(self):
        current_time = time.time()
        self.__solution_count = self.__solution_count + 1
        print(f'Solution {self.__solution_count}, time = {current_time - self.__start_time} s')
        print('  [', end=' ')
        for x in self.__solution:
            print(f'{self.value(x)}', end=' ')
        print(']')
        print('  [', end=' ')
        solution = []
        for i, x in enumerate(self.__solution):
            if self.value(x) == 1:
                solution.append(self.__a[i])
                print(f'{self.__a[i]}', end=' ')
        print(']')
        self.__all_solutions.append(solution)

In [ ]:
class Model:
    def __init__(self, a, tau):
        self.a = a
        self.tau = tau

        self.model = cp_model.CpModel()
        self.solver = cp_model.CpSolver()

        self.x = [self.model.new_bool_var(f"a{i} is used") for i in range(len(self.a))]
        y = [self.model.new_int_var(1, self.a[i], "") for i in range(len(self.a))]
        z = [self.model.new_int_var(1, self.a[i], "") for i in range(len(self.a))]

        for i in range(len(self.a)):
            self.model.add(y[i] == (self.a[i] - 1) * self.x[i] + 1)
            self.model.add(z[i] == (self.a[i] - 1) * (1 - self.x[i]) + 1)

        y_prod = self.model.new_int_var(1, tau, "")
        self.model.add_multiplication_equality(y_prod, y)
        for j in range(len(self.a)):
            y_prod_zj = self.model.new_int_var(1, tau * self.a[j], "")
            self.model.add_multiplication_equality(y_prod_zj, [z[j], y_prod])
            self.model.add(y_prod_zj >= self.tau * (1 - self.x[j]) + 1)

    def solve(self):
        self.solution_printer = SolutionPrinter(self.a, self.x)
        self.solver.parameters.enumerate_all_solutions = True
        #self.solver.parameters.log_search_progress = True
        self.solver.solve(self.model, self.solution_printer)

In [ ]:
# a = list(range(1, 5+1))
# tau = 10

# a = list(range(1, 10+1))
# tau = 50

#a = list(range(1, 20+1))
#tau = 100

a = [2] * 16 # 少し時間かかる
tau = 2 ** 8

print(f"a = {a}")
print(f"tau = {tau}")

a = [2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
tau = 256


In [ ]:
model = Model(a, tau)
model.solve()

Solution 1, time = 0.002668619155883789 s
  [ 1 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 2, time = 0.002994537353515625 s
  [ 1 1 0 0 0 0 0 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 3, time = 0.0032804012298583984 s
  [ 1 0 1 0 0 0 0 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 4, time = 0.0035753250122070312 s
  [ 1 0 0 1 0 0 0 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 5, time = 0.004120588302612305 s
  [ 1 0 0 0 1 0 0 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 6, time = 0.004403829574584961 s
  [ 1 0 0 0 0 1 0 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 7, time = 0.004693269729614258 s
  [ 1 0 0 0 0 0 1 0 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 8, time = 0.004969120025634766 s
  [ 1 0 0 0 0 0 0 1 0 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 9, time = 0.0052416324615478516 s
  [ 1 0 0 0 0 0 0 0 1 0 1 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 10, time = 0.005532741546630859 s
  [ 1 1 0 0 0 0 0 0 1 0 0 1 1 1 1 1 

Solution 35, time = 0.01325678825378418 s
  [ 1 1 0 1 0 0 0 0 0 0 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 36, time = 0.013541936874389648 s
  [ 1 0 1 1 0 0 0 0 0 0 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 37, time = 0.013814687728881836 s
  [ 1 1 1 0 0 0 0 0 0 0 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 38, time = 0.014087200164794922 s
  [ 1 0 1 0 0 0 0 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 39, time = 0.014358997344970703 s
  [ 1 1 0 0 0 0 0 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 40, time = 0.014653682708740234 s
  [ 1 0 0 1 0 0 0 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 41, time = 0.014929056167602539 s
  [ 1 0 0 0 1 0 0 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 42, time = 0.015198469161987305 s
  [ 1 0 0 0 0 1 0 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 43, time = 0.015476226806640625 s
  [ 1 0 0 0 0 0 1 0 0 1 0 1 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 44, time = 0.0157468318939209 s
  [ 1 0 0 0 0 0 0 1 0 1 0 1 1 1 1

Solution 72, time = 0.02360677719116211 s
  [ 1 0 1 1 0 0 0 0 0 1 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 73, time = 0.023884296417236328 s
  [ 1 1 1 0 0 0 0 0 0 1 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 74, time = 0.024158239364624023 s
  [ 1 1 1 1 0 0 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 75, time = 0.02444911003112793 s
  [ 1 0 1 1 1 0 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 76, time = 0.02472996711730957 s
  [ 1 1 0 1 1 0 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 77, time = 0.025014400482177734 s
  [ 1 1 1 0 1 0 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 78, time = 0.025297880172729492 s
  [ 1 0 1 0 1 1 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 79, time = 0.0275118350982666 s
  [ 1 1 0 0 1 1 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 80, time = 0.027802705764770508 s
  [ 1 0 0 1 1 1 0 0 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 81, time = 0.028090476989746094 s
  [ 1 1 0 1 0 1 0 0 0 0 0 0 1 1 1 1

Solution 102, time = 0.0340120792388916 s
  [ 1 0 0 0 1 1 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 103, time = 0.0343017578125 s
  [ 1 1 0 0 1 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 104, time = 0.03459763526916504 s
  [ 1 0 1 0 1 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 105, time = 0.034871816635131836 s
  [ 1 0 0 1 1 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 106, time = 0.03515291213989258 s
  [ 1 1 0 1 0 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 107, time = 0.03544497489929199 s
  [ 1 0 1 1 0 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 108, time = 0.035720109939575195 s
  [ 1 1 1 0 0 0 0 1 0 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 109, time = 0.03600430488586426 s
  [ 1 0 1 0 0 0 0 1 1 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 110, time = 0.03628087043762207 s
  [ 1 1 0 0 0 0 0 1 1 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 111, time = 0.03656888008117676 s
  [ 1 0 0 1 0 0 0 1 1 0 0 0 1 1 1

Solution 139, time = 0.04434561729431152 s
  [ 1 0 0 1 0 0 0 1 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 140, time = 0.044631004333496094 s
  [ 1 0 0 0 1 0 0 1 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 141, time = 0.04490518569946289 s
  [ 1 0 0 0 0 1 0 1 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 142, time = 0.045169830322265625 s
  [ 1 0 0 0 0 0 1 1 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 143, time = 0.04545426368713379 s
  [ 1 1 0 0 0 0 1 0 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 144, time = 0.04574894905090332 s
  [ 1 0 1 0 0 0 1 0 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 145, time = 0.04602479934692383 s
  [ 1 0 0 1 0 0 1 0 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 146, time = 0.04629778861999512 s
  [ 1 0 0 0 1 0 1 0 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 147, time = 0.04657340049743652 s
  [ 1 0 0 0 0 1 1 0 0 0 1 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 148, time = 0.04684901237487793 s
  [ 1 1 0 0 0 1 0 0 0 0 1 0 

...

Solution 12685, time = 3.7172863483428955 s
  [ 0 1 1 0 0 1 0 0 1 0 1 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12686, time = 3.717557430267334 s
  [ 0 1 1 0 0 0 0 0 1 0 1 1 1 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12687, time = 3.717804193496704 s
  [ 0 1 1 0 0 0 0 0 1 1 1 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12688, time = 3.718048334121704 s
  [ 0 1 1 0 1 0 0 0 1 0 1 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12689, time = 3.718294143676758 s
  [ 0 1 1 1 0 0 0 0 1 0 1 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12690, time = 3.718553304672241 s
  [ 0 1 1 1 0 0 0 0 1 0 1 0 1 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12691, time = 3.7188026905059814 s
  [ 0 1 1 1 0 1 0 0 1 0 1 0 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12692, time = 3.7190499305725098 s
  [ 0 1 1 1 0 0 0 0 1 1 1 0 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12693, time = 3.7192957401275635 s
  [ 0 1 1 1 1 0 0 0 1 0 1 0 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12694, time = 3.719557285308838 s
  [ 0 1 1 0 1 0 0 0 1 0 1 

Solution 12726, time = 3.7276813983917236 s
  [ 0 1 1 1 0 0 0 0 1 0 1 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12727, time = 3.7279369831085205 s
  [ 0 1 1 1 0 1 0 0 1 0 1 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12728, time = 3.7281851768493652 s
  [ 0 1 1 1 0 0 0 0 1 1 1 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12729, time = 3.7284352779388428 s
  [ 0 1 1 0 0 0 0 0 1 1 1 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12730, time = 3.728703022003174 s
  [ 0 1 1 0 0 1 0 0 1 1 1 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12731, time = 3.728972911834717 s
  [ 0 1 1 0 0 1 0 0 1 0 1 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12732, time = 3.7292234897613525 s
  [ 0 1 1 0 1 1 0 0 1 0 1 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12733, time = 3.729480266571045 s
  [ 0 1 1 0 1 0 0 0 1 0 1 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12734, time = 3.7297275066375732 s
  [ 0 1 1 0 1 0 0 0 1 1 1 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12735, time = 3.729975461959839 s
  [ 0 1 1 0 1 0 0 0 1 1 

Solution 12766, time = 3.7381889820098877 s
  [ 0 1 1 1 0 1 0 0 1 0 0 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12767, time = 3.738457441329956 s
  [ 0 1 1 1 0 1 0 0 1 0 0 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12768, time = 3.738722562789917 s
  [ 0 1 1 1 0 1 0 0 1 0 0 1 1 1 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12769, time = 3.7389822006225586 s
  [ 0 1 1 1 0 1 0 0 1 0 0 1 0 1 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12770, time = 3.739238977432251 s
  [ 0 1 1 1 0 1 0 0 1 1 0 1 0 1 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12771, time = 3.7395081520080566 s
  [ 0 1 1 1 0 1 0 0 1 1 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12772, time = 3.739752769470215 s
  [ 0 1 1 1 0 1 0 0 1 1 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12773, time = 3.739997625350952 s
  [ 0 1 1 1 0 1 0 0 1 1 0 1 0 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12774, time = 3.740241527557373 s
  [ 0 1 1 1 0 0 0 0 1 1 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12775, time = 3.7404935359954834 s
  [ 0 1 1 1 0 0 0 0 1 1 0 

Solution 12807, time = 3.748528480529785 s
  [ 0 1 1 0 1 1 0 0 1 1 0 1 0 1 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12808, time = 3.748927593231201 s
  [ 0 1 1 0 1 1 0 0 1 1 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12809, time = 3.7491934299468994 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 1 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12810, time = 3.7494606971740723 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 1 1 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12811, time = 3.749718189239502 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 0 1 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12812, time = 3.749967336654663 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 0 1 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12813, time = 3.7502098083496094 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12814, time = 3.750490665435791 s
  [ 0 1 1 0 1 0 0 0 1 1 0 1 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12815, time = 3.750746011734009 s
  [ 0 1 1 0 1 0 0 0 1 1 0 0 1 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12816, time = 3.7509946823120117 s
  [ 0 1 1 0 1 0 0 0 1 1 0 

Solution 12848, time = 3.7590365409851074 s
  [ 0 1 1 1 0 1 0 0 1 0 0 0 1 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12849, time = 3.7593023777008057 s
  [ 0 1 1 1 0 1 0 0 1 0 0 0 0 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12850, time = 3.7595815658569336 s
  [ 0 1 1 1 0 0 0 0 1 0 0 0 1 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12851, time = 3.7598443031311035 s
  [ 0 1 1 1 1 0 0 0 1 0 0 0 1 1 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12852, time = 3.7601006031036377 s
  [ 0 1 1 1 1 0 0 0 1 0 0 0 0 1 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12853, time = 3.760451316833496 s
  [ 0 1 1 1 1 0 0 0 1 0 0 0 1 1 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12854, time = 3.76069712638855 s
  [ 0 1 1 1 1 0 0 0 1 0 0 0 1 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12855, time = 3.7609376907348633 s
  [ 0 1 1 1 1 1 0 0 1 0 0 0 1 0 1 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12856, time = 3.7611777782440186 s
  [ 0 1 1 1 1 1 0 0 1 0 0 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12857, time = 3.761413097381592 s
  [ 0 1 1 1 1 1 0 0 1 0 

In [ ]:
pprint.pprint(model.solution_printer.all_solutions, indent=4)

[   [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2,

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

In [ ]:
print("Statistics")
print(f"  conflicts      : {model.solver.num_conflicts}")
print(f"  branches       : {model.solver.num_branches}")
print(f"  wall time      : {model.solver.wall_time} s")
print(f"  solutions found: {model.solution_printer.solution_count}")

Statistics
  conflicts      : 12
  branches       : 123172
  wall time      : 3.7648228610000003 s
  solutions found: 12870


## 定式化(MILP)

$x = [x_1, \dots, x_n]$ を 0-1 決定変数とする.
$x_i$ が $1$ のとき $a_i$ を採用し, $0$ のとき採用しない.

$$
w := \log(a_1) x_1 + \dots + \log(a_n) x_n
$$

とすると制約条件は以下のように書ける.

- $w \leq \log(\tau)$: 採用した $a_i$ の積が $\tau$ を超えない
- $w + \log(a_i) (1 - x_i) > \log(\tau) (1 - x_i) \quad (\forall i = 1, \dots, n)$: 採用しなかった $a_j$ を掛けたら $\tau$ を超えてしまう.

CP-SAT ソルバーは整数しか扱えないので $\log(a_i)$ や $\log(\tau)$ は適当にスケールして小数点以下を切り捨てることにする.
これによって誤差が出るかもしれない.

## 実装(MILP)

In [ ]:
class ModelLinear:
    def __init__(self, a, tau):
        self.a = a
        self.tau = tau
        base = 1000000
        self.log_a = [math.floor(math.log(ai) * base) for ai in a]
        self.log_tau = math.floor(math.log(self.tau) * base)
        self.model = cp_model.CpModel()
        self.solver = cp_model.CpSolver()
        self.x = [self.model.new_bool_var(f"a{i} is used") for i in range(len(self.a))]
        w = sum(a * x for a, x in zip(self.log_a, self.x))

        self.model.add(w <= self.log_tau)
        for a, x in zip(self.log_a, self.x):
            self.model.add(w + a * (1 - x) >= (self.log_tau + 1) * (1 - x))

    def solve(self):
        self.solution_printer = SolutionPrinter(self.a, self.x)
        self.solver.parameters.enumerate_all_solutions = True
        #self.solver.parameters.log_search_progress = True
        self.solver.solve(self.model, self.solution_printer)

In [ ]:
print(f"a = {a}")
print(f"tau = {tau}")

a = [2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
tau = 256


In [ ]:
model_linear = ModelLinear(a, tau)
model_linear.solve()

Solution 1, time = 0.0011174678802490234 s
  [ 0 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 2, time = 0.0014185905456542969 s
  [ 0 0 1 1 1 1 1 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 3, time = 0.0016977787017822266 s
  [ 0 1 0 1 1 1 1 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 4, time = 0.0019655227661132812 s
  [ 0 1 1 0 1 1 1 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 5, time = 0.002227783203125 s
  [ 0 1 1 1 0 1 1 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 6, time = 0.0024917125701904297 s
  [ 0 1 1 1 1 0 1 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 7, time = 0.0027658939361572266 s
  [ 0 1 1 1 1 1 0 1 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 8, time = 0.003028392791748047 s
  [ 0 1 1 1 1 1 1 0 1 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 9, time = 0.003398895263671875 s
  [ 0 1 1 1 1 1 1 1 0 1 0 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 10, time = 0.003676891326904297 s
  [ 0 0 1 1 1 1 1 1 0 1 1 0 0 0 0 0 

Solution 40, time = 0.011710166931152344 s
  [ 0 1 1 0 1 1 1 1 1 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 41, time = 0.011990785598754883 s
  [ 0 1 1 1 0 1 1 1 1 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 42, time = 0.012254476547241211 s
  [ 0 1 1 1 1 0 1 1 1 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 43, time = 0.012514829635620117 s
  [ 0 1 1 1 1 1 0 1 1 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 44, time = 0.012781858444213867 s
  [ 0 1 1 1 1 1 1 0 1 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 45, time = 0.013042449951171875 s
  [ 0 1 1 1 1 1 1 1 0 0 1 0 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 46, time = 0.013305425643920898 s
  [ 0 0 1 1 1 1 1 1 0 0 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 47, time = 0.013566017150878906 s
  [ 0 1 0 1 1 1 1 1 0 0 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 48, time = 0.01383662223815918 s
  [ 0 1 1 0 1 1 1 1 0 0 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 49, time = 0.01409769058227539 s
  [ 0 1 1 1 0 1 1 1 0 0 1 1 0 0 

Solution 77, time = 0.022060632705688477 s
  [ 0 0 0 1 0 1 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 78, time = 0.022335290908813477 s
  [ 0 1 0 1 0 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 79, time = 0.022596120834350586 s
  [ 0 0 1 1 0 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 80, time = 0.022954940795898438 s
  [ 0 1 1 0 0 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 81, time = 0.023245573043823242 s
  [ 0 0 1 0 1 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 82, time = 0.023543834686279297 s
  [ 0 1 0 0 1 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 83, time = 0.02384042739868164 s
  [ 0 0 0 1 1 0 1 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 84, time = 0.024103164672851562 s
  [ 0 1 0 1 1 0 0 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 85, time = 0.02434825897216797 s
  [ 0 0 1 1 1 0 0 1 1 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 86, time = 0.024591445922851562 s
  [ 0 1 1 0 1 0 0 1 1 1 1 1 0 0 

Solution 119, time = 0.032567501068115234 s
  [ 0 1 1 1 1 0 0 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 120, time = 0.032814741134643555 s
  [ 0 0 1 1 1 0 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 121, time = 0.033049583435058594 s
  [ 0 1 0 1 1 0 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 122, time = 0.03328442573547363 s
  [ 0 1 1 0 1 0 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 123, time = 0.033516883850097656 s
  [ 0 1 1 1 0 0 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 124, time = 0.03376007080078125 s
  [ 0 0 1 1 0 1 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 125, time = 0.03399658203125 s
  [ 0 1 0 1 0 1 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 126, time = 0.03423643112182617 s
  [ 0 1 1 0 0 1 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 127, time = 0.03447580337524414 s
  [ 0 0 1 0 1 1 1 1 0 1 1 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 128, time = 0.03476715087890625 s
  [ 0 1 0 0 1 1 1 1 0 1 1 1 0

Solution 161, time = 0.04287147521972656 s
  [ 0 1 1 1 0 1 1 1 1 0 0 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 162, time = 0.043343544006347656 s
  [ 0 1 1 1 1 0 1 1 1 0 0 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 163, time = 0.043784379959106445 s
  [ 0 1 1 1 1 1 0 1 1 0 0 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 164, time = 0.0440518856048584 s
  [ 0 1 1 1 1 1 1 0 1 0 0 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 165, time = 0.04431295394897461 s
  [ 0 1 1 1 1 1 1 1 0 0 0 1 0 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 166, time = 0.04457569122314453 s
  [ 0 0 1 1 1 1 1 1 0 0 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 167, time = 0.04484152793884277 s
  [ 0 1 0 1 1 1 1 1 0 0 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 168, time = 0.04510021209716797 s
  [ 0 1 1 0 1 1 1 1 0 0 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 169, time = 0.045358896255493164 s
  [ 0 1 1 1 0 1 1 1 0 0 0 1 1 0 0 0 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 170, time = 0.04562568664550781 s
  [ 0 1 1 1 1 0 1 1 0 0 0 1 

...

Solution 12689, time = 3.1968679428100586 s
  [ 1 1 1 1 1 1 0 1 0 0 0 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12690, time = 3.197188138961792 s
  [ 1 0 1 1 1 1 0 1 0 0 0 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12691, time = 3.1974258422851562 s
  [ 1 0 1 1 1 1 0 1 0 0 1 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12692, time = 3.197667121887207 s
  [ 1 0 1 1 1 1 0 1 1 0 0 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12693, time = 3.1979005336761475 s
  [ 1 1 1 1 1 0 0 1 1 0 0 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12694, time = 3.1981372833251953 s
  [ 1 0 1 1 1 0 0 1 1 0 0 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12695, time = 3.198397636413574 s
  [ 1 0 1 1 1 0 0 1 1 0 1 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12696, time = 3.198639392852783 s
  [ 1 1 1 1 1 0 0 1 0 0 1 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12697, time = 3.198873519897461 s
  [ 1 0 1 1 1 0 0 1 0 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12698, time = 3.1991074085235596 s
  [ 1 1 1 1 1 0 0 1 0 0 0

Solution 12732, time = 3.207318067550659 s
  [ 1 1 1 1 0 1 0 0 1 0 0 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12733, time = 3.2075560092926025 s
  [ 1 1 1 1 0 1 0 0 0 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12734, time = 3.2077999114990234 s
  [ 1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12735, time = 3.2080345153808594 s
  [ 1 0 1 1 1 0 0 0 1 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12736, time = 3.208266496658325 s
  [ 1 1 1 1 1 0 0 0 1 0 1 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12737, time = 3.2085018157958984 s
  [ 1 1 1 1 1 0 0 0 1 0 0 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12738, time = 3.208770990371704 s
  [ 1 1 1 1 1 0 0 0 0 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12739, time = 3.2090065479278564 s
  [ 1 0 1 1 1 1 0 0 0 0 1 0 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12740, time = 3.209245443344116 s
  [ 1 1 1 1 1 1 0 0 0 0 1 0 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12741, time = 3.209482431411743 s
  [ 1 1 1 1 1 1 0 0 0 0 0

Solution 12775, time = 3.2176737785339355 s
  [ 1 1 0 1 1 1 0 0 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12776, time = 3.2179152965545654 s
  [ 1 1 0 1 1 1 0 0 0 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12777, time = 3.218151330947876 s
  [ 1 0 0 1 1 1 0 0 1 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12778, time = 3.2183825969696045 s
  [ 1 1 0 1 1 1 0 0 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12779, time = 3.2186224460601807 s
  [ 1 0 0 1 1 1 0 0 1 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12780, time = 3.2189016342163086 s
  [ 1 0 0 1 1 1 0 1 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12781, time = 3.219137668609619 s
  [ 1 1 0 1 1 1 0 1 0 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12782, time = 3.219369649887085 s
  [ 1 0 0 1 1 1 0 1 0 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12783, time = 3.219606399536133 s
  [ 1 0 0 1 1 1 0 1 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12784, time = 3.2198405265808105 s
  [ 1 1 0 1 1 0 0 1 0 0 

Solution 12818, time = 3.2280173301696777 s
  [ 1 0 1 1 0 0 1 1 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12819, time = 3.228257179260254 s
  [ 1 0 1 1 0 0 1 1 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12820, time = 3.2284908294677734 s
  [ 1 0 1 1 0 1 1 1 0 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12821, time = 3.228759288787842 s
  [ 1 1 0 1 0 1 1 1 0 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12822, time = 3.229017496109009 s
  [ 1 0 0 1 0 1 1 1 0 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12823, time = 3.2292728424072266 s
  [ 1 0 0 1 0 1 1 1 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12824, time = 3.229555368423462 s
  [ 1 0 0 1 0 1 1 1 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12825, time = 3.229797124862671 s
  [ 1 1 0 1 0 0 1 1 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12826, time = 3.2300305366516113 s
  [ 1 0 0 1 0 0 1 1 1 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12827, time = 3.230264186859131 s
  [ 1 0 0 1 0 0 1 1 1 0 1 

Solution 12861, time = 3.238473415374756 s
  [ 1 0 1 1 0 0 1 0 1 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12862, time = 3.238746166229248 s
  [ 1 0 1 1 0 0 1 0 1 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12863, time = 3.2390072345733643 s
  [ 1 1 1 1 0 0 1 0 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12864, time = 3.239267110824585 s
  [ 1 0 1 1 0 0 1 0 0 0 1 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12865, time = 3.2395215034484863 s
  [ 1 1 1 1 0 0 1 0 0 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12866, time = 3.2398123741149902 s
  [ 1 0 1 1 1 0 1 0 0 0 0 1 0 0 1 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12867, time = 3.2400498390197754 s
  [ 1 1 1 1 1 0 1 0 0 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12868, time = 3.240283966064453 s
  [ 1 0 1 1 1 0 1 0 0 0 1 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12869, time = 3.2405171394348145 s
  [ 1 0 1 1 1 0 1 0 1 0 0 1 0 0 0 1 ]
  [ 2 2 2 2 2 2 2 2 ]
Solution 12870, time = 3.2407569885253906 s
  [ 1 0 1 1 1 1 1 0 0 0 

In [ ]:
pprint.pprint(model_linear.solution_printer.all_solutions, indent=4)

[   [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2,

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

[2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 2, 2, 2, 2, 2],
    [2, 2, 2, 

In [ ]:
print('Statistics')
print(f' conflicts : {model_linear.solver.num_conflicts}')
print(f' branches : {model_linear.solver.num_branches}')
print(f' wall time : {model_linear.solver.wall_time} s')
print(f' solutions found: {model_linear.solution_printer.solution_count}')

Statistics
 conflicts : 8
 branches : 112896
 wall time : 3.240941072 s
 solutions found: 12870
